# Generalised Algebraic Data Types

> Juan Pablo Yamamoto  
> jpyamamoto\[at\]ciencias.unam.mx  
> Lógica Computacional II. Semestre 2025-1.

## Requisitos Previos

In [1]:
{-# LANGUAGE GADTs #-}

## Codificación de Naturales como Tipos

Codificamos los tipos naturales al nivel de tipos, no nos interesa que tengamos términos que los representen (constructores).

In [2]:
data Zero
data Succ n

## Vectores

Teniendo números naturales, podemos codificar los vectores como listas dependientes de un natural.

- Un vector es una lista de tamaño fijo y finito.
- Vector vacío
- Dado un vector `xs` de tamaño `n`, `Cons x xs` es un vector de tamaño `n+1`

In [3]:
data Vec a n where
    Void :: Vec a Zero
    Cons :: a -> Vec a n -> Vec a (Succ n)

In [4]:
instance Show a => Show (Vec a n) where
    show Void = "Void"
    show (Cons x xs) = "(Cons " ++ show x ++ " " ++ show xs ++ ")"

In [5]:
:t Void

Void :: forall a. Vec a Zero

In [6]:
:t Cons 1 Void
:t Cons 1 (Cons 2 Void)

Cons 1 Void :: forall {a}. Num a => Vec a (Succ Zero)

Cons 1 (Cons 2 Void) :: forall {a}. Num a => Vec a (Succ (Succ Zero))

## Funciones seguras

Definición de `head`:

In [7]:
headVec :: Vec a (Succ n) -> a
headVec (Cons x _) = x

In [8]:
:t headVec (Cons 1 Void)

headVec (Cons 1 Void) :: forall {a}. Num a => a

In [9]:
:t headVec Void

: 

In [10]:
:t head []

head [] :: forall {a}. a

In [11]:
head []

: 

Definición de `tail`:

In [12]:
tailVec :: Vec a (Succ n) -> Vec a n
tailVec (Cons _ xs) = xs

In [13]:
:t tailVec (Cons 1 Void)

tailVec (Cons 1 Void) :: forall {a}. Num a => Vec a Zero

In [14]:
:t tailVec Void

: 

In [15]:
:t tail []

tail [] :: forall {a}. [a]

In [16]:
tail []

: 

Definición de `map`:

In [17]:
mapVec :: (a -> b) -> Vec a n -> Vec b n
mapVec f Void = Void
mapVec f (Cons x xs) = Cons (f x) (mapVec f xs)

## Append

¿Cuál sería el tipo que corresponde?

```haskell
append :: Vec a m -> Vec a n -> Vec a ???
```

### Suma de Naturales

In [18]:
data Sum m n s where
    SumZero :: Sum Zero n n
    SumSucc :: Sum m n s -> Sum (Succ m) n (Succ s)

In [19]:
instance Show (Sum m n s) where
    show SumZero = "SumZero"
    show (SumSucc n) = "(SumSucc " ++ show n ++ ")"

Damos evidencia de los tipos, para definir la suma.

In [20]:
append :: Sum m n s -> Vec a m -> Vec a n -> Vec a s
append SumZero Void ys = ys
append (SumSucc p) (Cons x xs) ys = Cons x (append p xs ys)

In [23]:
append SumZero Void (Cons 2 Void)

(Cons 2 Void)

In [22]:
:t SumSucc SumZero

SumSucc SumZero :: forall {s}. Sum (Succ Zero) s (Succ s)

In [25]:
append (SumSucc (SumSucc SumZero)) (Cons 1 (Cons 2 (Cons 3 Void))) (Cons 4 Void)

: 

In [26]:
fromList :: [a] -> Vec a n
fromList [] = Void
fromList (x:xs) = Cons x (fromList xs)

Line 2: Use foldr
Found:
fromList [] = Void
fromList (x : xs) = Cons x (fromList xs)
Why not:
fromList xs = foldr Cons Void xs

: 